# OMMX Python SDK 1.5.0

[![Static Badge](https://img.shields.io/badge/GitHub_Release-Python_SDK_1.5.0-blue?logo=github)](https://github.com/Jij-Inc/ommx/releases/tag/python-1.5.0)

This notebook describes the new features. Please refer the GitHub release note for the detailed information.

## Evaluation and Partial Evaluation

From the first release of OMMX, `ommx.v1.Instance` supports `evaluate` method to produce `Solution` message

In [1]:
from ommx.v1 import Instance, DecisionVariable

# Create an instance of the OMMX API
x = DecisionVariable.binary(1)
y = DecisionVariable.binary(2)

instance = Instance.from_components(
    decision_variables=[x, y],
    objective=x + y,
    constraints=[x + y <= 1],
    sense=Instance.MINIMIZE
)
solution = instance.evaluate({1: 1, 2: 0})

In [2]:
solution.decision_variables

kind value lower upper name subscripts description
                                                        
id                                                      
1   binary   1.0   0.0   1.0              []            
2   binary   0.0   0.0   1.0              []

From Python SDK 1.5.0, `Function` and its base classes, `Linear`, `Quadratic`, and `Polynomial` also support `evaluate` method:

In [3]:
f = 2*x + 3*y
value, used_ids = f.evaluate({1: 1, 2: 0})
print(f"{value=}, {used_ids=}")

value=2.0, used_ids={1, 2}


This returns evaluated value of the function and used decision variable IDs. If some decision variables are lacking, the `evaluate` method raises an exception:

In [4]:
try:
    f.evaluate({3: 1})
except RuntimeError as e:
    print(e)

Variable id (1) is not found in the solution


In addition, there is `partial_evaluate` method

In [5]:
f2, used_ids = f.partial_evaluate({1: 1})
print(f"{f2=}, {used_ids=}")

f2=Linear(3*x2 + 2), used_ids={1}


This creates a new function by substituting `x = 1`. `partial_evaluate` is also added to `ommx.v1.Instance` class:

In [6]:
new_instance = instance.partial_evaluate({1: 1})
new_instance.objective

Function(x2 + 1)

This method will be useful for creating a problem with fixing specific decision variables.